In [64]:
import pandas as pd 
import matplotlib.pyplot as plt
import numpy as np
import hairball
import ast
import csv

In [130]:

columns_name = ['p_ID', 'Default_Names', 'Dead_Code', 'Total_Blocks']
df_code = pd.DataFrame([], columns= columns_name)


In [131]:
filepath = 'ScratchDataset/code.csv'
    
with open(filepath) as fp:
    head = fp.readline() #Read head
    head = list(ast.literal_eval(head)[0:8])
    
    line = fp.readline() #Read the first line to have the first id
    
    project_id = line.split(",")[0] #First id
    
    new_project = True
        
    while new_project:
        with open('aux.csv', 'w') as f:
            
            wr = csv.writer(f, quoting=csv.QUOTE_ALL)
            wr.writerow(head) #Write head
            
            try:
                line = list(ast.literal_eval(line)[0:8])  #Only the columns I want
                wr.writerow(line) #Write the first line
            except:
                line = "error"
                

            while line:
            
                line = fp.readline()
                if not line:
                    new_project = False     #End of the document, save the last project and exit
                    
                new_id = line.split(",")[0]

                if new_id == project_id:     #Is the same id -> Same project
                    try:
                        line = list(ast.literal_eval(line)[0:8]) 
                        wr.writerow(line)
                    except:
                        line = "error"
                else:
                    f.close()                
                    #Analyze an unique project
                    df_aux = pd.read_csv('aux.csv')

                    #Default names
                    sprite_names = df_aux['sprite-name'].unique()
                    default_names = 0
                    for name in sprite_names:
                        if 'Sprite' in str(name):
                            default_names += 1

                    #Dead code
                    df_id = df_aux[['script-rank', 'total-blocks']]
                    df_id = df_id.groupby(['script-rank', 'total-blocks']).size().reset_index()

                    dead_code = df_id['total-blocks'].loc[df_id['total-blocks'] == 1].count()

                    #Total Blocks
                    total_blocks = df_id[0].sum()

                    #Save the result
                    data = [[project_id, default_names, dead_code, total_blocks]]
                    df_2 = pd.DataFrame(data, columns=columns_name)
                    df_code = df_code.append(df_2)

                    project_id = new_id 
                    break
                

df_code

p_ID Default_Names Dead_Code Total_Blocks
0   "10519701"             3         0            9
0   "10541430"             0         0           85
0   "10942522"             0         1          216
0   "11823040"             0         0            3
0   "11828235"             1         5           41
0   "12030146"            13         4          281
0   "12237615"             3         3           41
0   "12256407"             1         0            9
0   "12441584"             3         0          126
0   "12596438"            20         0          172
0   "12597047"             1         0            2
0   "12597397"             1         0            2
0   "12683181"             7         0          111
0   "13223646"             0         0          427
0   "13357844"             0         1          139
0   "13618241"             2         0            6
0   "14073938"             2         3          112
0   "14125270"            15         0          293
0   "14137046"             0         0          359
0   "14161862"             5         2          103
0   "14742679"             1         0           29
0   "14860321"            16         0          160
0   "15032542"             1         0           97
0   "15086346"             1         1           87
0   "15118716"             1         0           10
0   "15141278"             0         1            9
0   "15163360"             2         3           33
0   "15187520"             1         0           41
0   "15296441"             0         0           36
0   "15529084"             1         5           75
..         ...           ...       ...          ...
0   "99965000"             1         0           45
0   "99965005"             0         0           26
0   "99965007"             1         2           29
0   "99965010"             1         0           41
0   "99965016"             1         0            6
0   "99965020"             1         6           31
0   "99965032"             1         2           30
0   "99965036"             1         0            6
0   "99965057"             0         0           26
0   "99965058"             1         1           30
0   "99965063"             0         1           10
0   "99965066"             2         0           24
0   "99965160"             3         0           51
0   "99965177"             1         0           27
0   "99965204"             1         0           41
0   "99965250"             0         0            5
0   "99965261"             0         0           14
0   "99965283"             0         8          431
0   "99965293"             1         0           14
0   "99965334"             0         0           11
0   "99965338"             0         0            6
0   "99965352"             0         0            3
0   "99965354"             1         0           48
0   "99965400"             1         0           12
0   "99965453"             1         0            3
0   "99965457"             3         0          419
0   "99965561"             1         0            6
0   "99965607"             3         0           51
0   "99965707"             0        14         1619
0   "99965776"             0         0            7

[233547 rows x 4 columns]

In [134]:
df_code.to_csv('final_code.csv', index=None)

In [137]:
#Read the csv without wrong projects

df_projects = pd.read_csv('ScratchDataset/final_code.csv')
df_metadata = pd.read_csv('ScratchDataset/metadata_noerrors.csv')

df_projects.shape, df_metadata.shape

((233491, 4), (231050, 21))

In [138]:
#Clean df

df_data = df_metadata.drop(['project-name', 'username', 'total-views', 'total-remixes', 'total-favorites',
                            'total-loves', 'is-remix', 'Remixed-from', 'URL'], axis=1)

In [143]:
#Create new df with both data and code

columns_name = ['p_ID', 'Mastery', 'Default_Names', 'Duplicated_Code', 'Dead_Code', 'Attribute_Initialization',
                'Abstraction', 'Parallelism', 'Logic', 'Synchronization', 'Flow Control', 'User Interactivity',
                'Data Representation', 'Total Blocks']

df = pd.DataFrame([], columns= columns_name)


for index,row in df_projects.iterrows():
    
    id = int(row['p_ID'])
    print id
    
    #Check if the id is not wrong in metadata
    if not df_data.where(df_data['p_ID'] == id).dropna().empty:
        
        #Matery
        mastery = df_data['Mastery'].loc[df_data['p_ID'] == id].item()
        
        #Total Blocks
        total_blocks = row['Total_Blocks']#.loc[df_code['p_ID'] == id].unique().item()
        
        #Default Names
        default_names = row['Default_Names']#.loc[df_code['p_ID'] == id].unique().item()
        
        #Duplicated Code
        dup_code = df_data['Clones'].loc[df_data['p_ID'] == id].item()
        
        #Dead Code
        dead_code = row['Dead_Code']#.loc[df_code['p_ID'] == id].unique().item()
        
        #Categories
        abstraction = df_data['Abstraction'].loc[df_data['p_ID'] == id].item()
        parallelism = df_data['Parallelism'].loc[df_data['p_ID'] == id].item()
        logic = df_data['Logic'].loc[df_data['p_ID'] == id].item()
        synchroniz = df_data['Synchronization'].loc[df_data['p_ID'] == id].item()
        flow_control = df_data['FlowControl'].loc[df_data['p_ID'] == id].item()
        user_interac = df_data['UserInteractivity'].loc[df_data['p_ID'] == id].item()
        data_repr = df_data['DataRepresentation'].loc[df_data['p_ID'] == id].item()
        
        data = [[id, mastery, default_names, dup_code, dead_code, '',
                 abstraction, parallelism, logic, synchroniz, flow_control, user_interac, data_repr,
                 total_blocks]]
        
        df_2 = pd.DataFrame(data, columns = columns_name)
        df = df.append(df_2)
        
df           


10519701
10541430
10942522
11823040
11828235
12030146
12237615
12256407
12441584
12596438
12597047
12597397
12683181
13223646
13357844
13618241
14073938
14125270
14137046
14161862
14742679
14860321
15032542
15086346
15118716
15141278
15163360
15187520
15296441
15529084
15548188
15591364
15592031
15649432
15819791
15819951
16180058
16198429
16198525
16306675
16661772
16661794
16661984
16751890
16767928
16774433
17062315
17290000
17386637
17622951
17647115
17816709
18312831
18560469
18560642
18636660
18637871
18675494
18711726
18763210
18806652
18851372
18856080
18956179
19281509
19346754
19347202
19531164
19534949
19589342
19799958
20058771
20522740
20708751
21003299
21019413
21086973
21114832
21194845
21349661
21476971
21477255
21482185
21532395
21578441
21667944
21672166
21883410
21890116
21915960
22175345
22244288
22321403
22335593
22371439
22416667
22593858
22656427
22705735
22707529
22890514
23012151
23105860
23248451
23314974
23341439
23442969
23476512
23625729
23783300
23809738
2

62048560
62050404
62052128
62065184
62070302
62076846
62079856
62080490
62197046
62239456
62256746
62262954
62303268
62371622
62374770
62488770
62505930
62537918
62557982
62579570
62597294
62599884
62602238
62605842
62625230
62688614
62730664
62772878
62821894
62904456
62924088
62927100
62944624
62997550
63083140
63092156
63095536
63115904
63179322
63182028
63204362
63208464
63216534
63299544
63309772
63331264
63332314
63339136
63389308
63393044
63458244
63483562
63489626
63491468
63497530
63500398
63509160
63520970
63532024
63572214
63583108
63634238
63718122
63726318
63802074
63820734
63827286
63839642
63841116
63907018
63940210
63966212
63980394
64033414
64083000
64104958
64132318
64143690
64191722
64194710
64196992
64268116
64295556
64438746
64448868
64471320
64479242
64527694
64537158
64611890
64648936
64650180
64727000
64730658
64753680
64789204
64803512
64804910
64853288
64871620
64879300
64927536
64939038
64961006
64986304
65062714
65070670
65083086
65100806
65145888
65190980
6

79128816
79149214
79158218
79162248
79176174
79210406
79227440
79230054
79231148
79234322
79241512
79246118
79256256
79275844
79295208
79323518
79332412
79358330
79373492
79377150
79408942
79415400
79471908
79501054
79513250
79526832
79528360
79554984
79562928
79563048
79572988
79576710
79594748
79594974
79599850
79621524
79628418
79652562
79671428
79693910
79722934
79738800
79743006
79777052
79787150
79787928
79794720
79801664
79809448
79842742
79859604
79860506
79866896
79866908
79938910
79956516
79997652
79998338
80010700
80049464
80055772
80067962
80069930
80085108
80085808
80094238
80097460
80116770
80119682
80123090
80126738
80131620
80138676
80143330
80157440
80161476
80166812
80198764
80200920
80201898
80204088
80204980
80206898
80206964
80207970
80208124
80212800
80232174
80238332
80240364
80261662
80265210
80268246
80283858
80286048
80307762
80310026
80312994
80314500
80340608
80383040
80450306
80476698
80492080
80496168
80500408
80505774
80507256
80537118
80544984
80551726
8

87108096
87108221
87118263
87122125
87123215
87124284
87124964
87125264
87129680
87130234
87132748
87134823
87137700
87139214
87140777
87143169
87144647
87154271
87158176
87161424
87162310
87168323
87169461
87172246
87174916
87176578
87185126
87186305
87186968
87187011
87187352
87191014
87191397
87205313
87209082
87211407
87214258
87217245
87226108
87226215
87226570
87227191
87228282
87229341
87237275
87239625
87245956
87253543
87254939
87258571
87258886
87259884
87263532
87266129
87271845
87273772
87285240
87292060
87292371
87293045
87296451
87298091
87302017
87302398
87302432
87309843
87319642
87327327
87332416
87334391
87336344
87338501
87338539
87338556
87338662
87340107
87340293
87342303
87342400
87344313
87347049
87349097
87357599
87357710
87360542
87361220
87370105
87371853
87373333
87374928
87376783
87380397
87381103
87382797
87385757
87385909
87386899
87397006
87404912
87410083
87410702
87418933
87419199
87419405
87421844
87422813
87426542
87430870
87431013
87431498
87437890
8

89690334
89690563
89690632
89690662
89690746
89690923
89690938
89690971
89692393
89703490
89707965
89710853
89713748
89713947
89717707
89717818
89721094
89722853
89722905
89724459
89728700
89728944
89730959
89732595
89734046
89734941
89735087
89736645
89738289
89740604
89749842
89752035
89752993
89754234
89755126
89762529
89765696
89766631
89768495
89769076
89772972
89776760
89777384
89777404
89781983
89784264
89784389
89784499
89785409
89786819
89789733
89791275
89791465
89794401
89794928
89797136
89802075
89802763
89803670
89807853
89811193
89811205
89813099
89814314
89819433
89820336
89820449
89820617
89820632
89820692
89820888
89821410
89821423
89821490
89821508
89821511
89821513
89821517
89821520
89821540
89822328
89822487
89822517
89822518
89822622
89822630
89822706
89823078
89825526
89825860
89826949
89827089
89827397
89827897
89827910
89828509
89828528
89829880
89832331
89835827
89845960
89848055
89848668
89854576
89855016
89855242
89857220
89859140
89859196
89859208
89859223
8

...

99942091
99942104
99942107
99942113
99942124
99942128
99942130
99942135
99942171
99942173
99942174
99942185
99942200
99942226
99942234
99942237
99942242
99942243
99942248
99942261
99942269
99942272
99942285
99942289
99942290
99942292
99942309
99942316
99942318
99942333
99942339
99942348
99942352
99942363
99942370
99942386
99942397
99942399
99942402
99942406
99942407
99942419
99942426
99942429
99942437
99942443
99942455
99942460
99942475
99942484
99942489
99942490
99942507
99942509
99942512
99942515
99942516
99942526
99942535
99942539
99942543
99942552
99942558
99942564
99942573
99942577
99942581
99942592
99942609
99942614
99942617
99942634
99942646
99942649
99942653
99942667
99942674
99942684
99942691
99942702
99942706
99942732
99942743
99942749
99942756
99942759
99942770
99942771
99942774
99942784
99942787
99942791
99942794
99942804
99942811
99942817
99942818
99942832
99942836
99942840
99942850
99942864
99942869
99942873
99942874
99942887
99942893
99942896
99942906
99942907
99942919
9

99949153
99949156
99949161
99949173
99949189
99949194
99949200
99949202
99949207
99949208
99949211
99949214
99949218
99949236
99949237
99949247
99949273
99949279
99949291
99949302
99949317
99949323
99949332
99949360
99949366
99949367
99949373
99949383
99949384
99949387
99949397
99949400
99949402
99949410
99949434
99949436
99949437
99949441
99949442
99949446
99949469
99949472
99949478
99949480
99949482
99949491
99949495
99949512
99949513
99949515
99949522
99949527
99949531
99949546
99949551
99949552
99949556
99949559
99949564
99949580
99949589
99949600
99949615
99949622
99949632
99949641
99949647
99949648
99949650
99949658
99949660
99949681
99949685
99949697
99949700
99949704
99949710
99949711
99949714
99949728
99949736
99949775
99949782
99949785
99949787
99949794
99949798
99949801
99949806
99949807
99949841
99949855
99949865
99949868
99949869
99949878
99949885
99949891
99949903
99949909
99949919
99949921
99949932
99949946
99949953
99949956
99949960
99949971
99949972
99949976
99949980
9

99956019
99956035
99956037
99956042
99956045
99956055
99956059
99956066
99956069
99956075
99956082
99956097
99956101
99956106
99956122
99956126
99956127
99956130
99956136
99956141
99956151
99956154
99956160
99956176
99956203
99956207
99956240
99956285
99956294
99956304
99956316
99956318
99956325
99956336
99956339
99956343
99956358
99956360
99956375
99956381
99956386
99956415
99956431
99956439
99956461
99956468
99956481
99956483
99956493
99956529
99956531
99956536
99956538
99956540
99956542
99956544
99956560
99956561
99956587
99956606
99956619
99956621
99956628
99956631
99956636
99956644
99956681
99956697
99956699
99956713
99956714
99956724
99956729
99956736
99956744
99956778
99956791
99956794
99956795
99956802
99956811
99956822
99956834
99956837
99956842
99956858
99956861
99956869
99956879
99956881
99956897
99956898
99956924
99956958
99956981
99956986
99957005
99957023
99957028
99957031
99957036
99957038
99957042
99957046
99957052
99957064
99957065
99957069
99957075
99957077
99957088
9

99963440
99963445
99963452
99963470
99963477
99963487
99963492
99963496
99963549
99963575
99963591
99963604
99963606
99963616
99963625
99963641
99963654
99963661
99963663
99963676
99963696
99963711
99963712
99963739
99963747
99963768
99963795
99963798
99963824
99963832
99963834
99963837
99963851
99963886
99963887
99963896
99963921
99963926
99963936
99963939
99963954
99963957
99963962
99963991
99964012
99964014
99964015
99964020
99964030
99964042
99964043
99964050
99964070
99964091
99964094
99964102
99964112
99964117
99964118
99964123
99964155
99964198
99964213
99964250
99964273
99964275
99964289
99964318
99964320
99964322
99964331
99964333
99964334
99964335
99964336
99964344
99964345
99964374
99964377
99964379
99964381
99964388
99964392
99964396
99964399
99964404
99964406
99964417
99964496
99964512
99964516
99964524
99964527
99964577
99964581
99964582
99964610
99964621
99964640
99964641
99964668
99964684
99964687
99964696
99964713
99964754
99964835
99964870
99964887
99964892
99964934
9

p_ID Mastery Default_Names Duplicated_Code Dead_Code  \
0   60002538       3             1               0         0   
0   60034304      16             0               0         4   
0   60058876      10             1               0         0   
0   60063608       8             3               1         2   
0   60068444       6             1               0         0   
0   60074986      19             1              10         1   
0   60082620      14             2               2         2   
0   60122018      15             0               0         0   
0   60122926       6             0               0         0   
0   60145364      16            16              11         0   
0   60204614       4             0               0         0   
0   60225348       6             2               0         0   
0   60229414       5             1               0         0   
0   60234624       9             0               0         1   
0   60295774      11             5               0         0   
0   60338738      11             9               1         0   
0   60440188      18             5              14        71   
0   60505632      16             5               1         3   
0   60530658      16             0               1         0   
0   60531878       7             1               0         0   
0   60538568      16             0               0         2   
0   60601472       6             1               0         1   
0   60640752      16             7               0        19   
0   60660644       7             2               0         0   
0   60664714      20             0               1         0   
0   60703742      13             7               2         0   
0   60709712      12             4               0         1   
0   60771904      21             1               5        34   
0   60817948       4             0               0         0   
0   60819578       4             0               0         0   
..       ...     ...           ...             ...       ...   
0   99965000       7             1               0         0   
0   99965005       7             0               0         0   
0   99965007       5             1               0         2   
0   99965010       5             1               0         0   
0   99965016       5             1               0         0   
0   99965020       6             1               0         6   
0   99965032       7             1               0         2   
0   99965036       7             1               0         0   
0   99965057       5             0               0         0   
0   99965058       8             1               0         1   
0   99965063       6             0               0         1   
0   99965066       8             2               0         0   
0   99965160      17             3               0         0   
0   99965177       7             1               0         0   
0   99965204       9             1               0         0   
0   99965250       5             0               0         0   
0   99965261       7             0               0         0   
0   99965283      15             0               1         8   
0   99965293       5             1               0         0   
0   99965334       6             0               0         0   
0   99965338       5             0               0         0   
0   99965352       3             0               0         0   
0   99965354      10             1               0         0   
0   99965400       7             1               0         0   
0   99965453       2             1               0         0   
0   99965457      13             3               1         0   
0   99965561       0             1               0         0   
0   99965607      17             3               0         0   
0   99965707      20             0               4        14   
0   99965776       7             0               0         0   

   Attribute_Initialization Abstraction

In [144]:
df.to_csv('final_dataset_3.csv', index=None)